# Preparation

In [0]:
#@title Install gspread
!pip install --upgrade -q gspread

In [0]:
#@title Import Strava activitities from Google Sheets

from google.colab import auth
auth.authenticate_user()

import gspread
from oauth2client.client import GoogleCredentials

gc = gspread.authorize(GoogleCredentials.get_application_default())

worksheet = gc.open('Strava 2018-07-02').sheet1

# get_all_values gives a list of rows.
rows = worksheet.get_all_values()

# Convert to a DataFrame and render.
import pandas as pd
activities_raw = pd.DataFrame.from_records(rows[1:], columns=rows[0]);

In [0]:
#@title Index activities, convert data types, convert units
activities = activities_raw.copy()

# Project
activities = activities[['date', 'type', 'distance', 'elapsed_time', 'commute', 'name']]

# Set data types
activities['distance'] = activities['distance'].astype(float)
activities['elapsed_time'] = activities['elapsed_time'].astype(float)
activities['commute'] = activities['commute'].apply(lambda x: 1 if x == 'TRUE' else 0).astype(int)

# Convert units
activities['distance'] = activities['distance'] / 1000
activities['elapsed_time'] = activities['elapsed_time'] / 60

# Number of activities (at this aggregation level, trivially 1)
activities['count'] = 1

# Index
activities['date'] = pd.to_datetime(activities_raw['date'])
activities.set_index(['date', 'type'], inplace=True)

In [0]:
#@title Define formatters for readability
formatters = {
    'distance': '{:.0f}km'.format,
    'elapsed_time':' {:.0f}min'.format,
}

detailed_formatters = {
    'distance': '{:.1f}km'.format,
    'elapsed_time':' {:.1f}min'.format,
}

# Exploration

In [0]:
#@title Print a few random activities
print(
    activities[['distance', 'elapsed_time', 'commute', 'count']]
      .sample(5)
      .sort_index()
      .to_string(formatters=formatters))

In [0]:
#@title Print totals
print(
    activities
      .groupby(level='type')
      .sum()
      .sort_values(by='count', ascending=False)
      .to_string(formatters=formatters))

In [0]:
#@title Show date range

first_date = activities.index.levels[0].min()
last_date = activities.index.levels[0].max()
print('Activities recorded from %s to %s, total of %d days.' % (
    first_date.strftime('%Y-%m-%d'),
    last_date.strftime('%Y-%m-%d'),
    (last_date - first_date).days))

In [0]:
#@title Activities with the longest distance
print(
    activities['distance']
        .groupby('type').nlargest(3)
        .to_string(float_format='%.1fkm'))

In [0]:
#@title Activities with the longest duration
print(
    (activities['elapsed_time']
        .groupby('type').nlargest(4) / 60)
        .to_string(float_format='%.1fh'))

In [0]:
#@title Summarize by day and activity type
import numpy as np

activities_by_day_type = (
    activities
        .groupby([pd.Grouper(freq='D', level=0), 'type'])
        .sum())

activities_by_day_type = (
    activities_by_day_type
        .reset_index(level='type')
        .to_period('D')
        .reset_index()
        .set_index(['date', 'type']))

first_day = activities_by_day_type.index.levels[0].min()
last_day = activities_by_day_type.index.levels[0].max()
days = pd.period_range(first_day, last_day, freq='D')
types = activities_by_day_type.index.levels[1].unique()
index = pd.MultiIndex.from_product([days, types], names=['day', 'type'])
activities_by_day_type = activities_by_day_type.reindex(index, fill_value=0)

In [0]:
#@title Print a few days
print(activities_by_day_type.tail(12).to_string(formatters=formatters))

In [0]:
#@title Activities by day
activities_by_day = activities_by_day_type.groupby('day').sum()

In [0]:
#@title Activities by type
activities_by_type = activities_by_day_type.groupby('type').sum()

In [0]:
#@title Daily average
print(
    activities_by_day[['distance', 'elapsed_time']]
        .mean()
        .to_frame('mean')
        .T
        .to_string(formatters=detailed_formatters))

In [0]:
#@title Quick sanity check

print("average distance per day: %.1fkm" % (
    activities['distance'].sum() /
    (last_day - first_day)))
print("average time per day: %.1fmin" % (
    activities['elapsed_time'].sum() /
    (last_day - first_day)))

In [0]:
#@title Find days, months, quarters, years with extremes

frequencies = ['D', 'M', 'Q', 'Y']

for f in frequencies:
  extremes_by_type = (
    activities_by_day_type
      .unstack('type')
      .groupby(pd.Grouper(freq=f)).sum()
      .agg(['idxmax', 'max']))
  extremes_by_type.index = [f, 'max']

  print(
    extremes_by_type.T
      .unstack(level=0)
      .swaplevel(axis=1)
      .sort_index(axis=1))
  print('freq=%s\n' % f)

In [0]:
#@title Weekdays with largest means
weekday_abbr = 'Mon Tue Wed Thu Fri Sat Sun'.split()
print(
    activities_by_day_type[['distance', 'elapsed_time', 'commute', 'count']]
        .unstack('type')
        .groupby(lambda d: weekday_abbr[d.weekday]).mean()
        .agg(['idxmax', 'max'])
        .T.unstack(level=0)
        .swaplevel(axis=1).sort_index(axis=1))

In [0]:
#@title Months of the year with largest means
months = 'Jan Feb Mar Apr May Jun Jul Aug Sep Oct Nov Dec'.split()
print(
    activities_by_day_type[['distance', 'elapsed_time', 'commute', 'count']]
        .unstack('type')
        .groupby(pd.Grouper(freq='M')).sum()
        .groupby(lambda m: months[m.month-1]).mean()
        .agg(['idxmax', 'max'])
        .T.unstack(level=0)
        .swaplevel(axis=1).sort_index(axis=1))

In [0]:
#@title Quarters of the year with largest means
print(
    activities_by_day_type[['distance', 'elapsed_time', 'commute', 'count']]
        .unstack('type')
        .groupby(pd.Grouper(freq='Q')).sum()
        .groupby(lambda d: "Q%d" % d.quarter).mean()
        .agg(['idxmax', 'max'])
        .T.unstack(level=0)
        .swaplevel(axis=1).sort_index(axis=1))

# Plotting

In [0]:
#@title Plot running activity, quarterly, summed
import matplotlib.pyplot as plt
from matplotlib.ticker import StrMethodFormatter

fig, (ax1, ax2, ax3) = (
    plt.subplots(
        nrows=3, ncols=1,
        sharex=True, sharey=False,
        figsize=(8.025, 10)))

runs_q_sum = (
    activities.loc[(slice(None), 'Run'), :]
        .reset_index('type', drop=True)
        .to_period('D')
        .groupby(pd.Grouper(freq='Q')).sum())

runs_q_sum['distance'].plot(ax=ax1, kind='bar', color='#7799cc')
ax1.set_ylabel('km')
ax1.set_title('Distance')

(runs_q_sum['elapsed_time'] / 60).plot(ax=ax2, kind='bar', color='#7799cc')
ax2.set_ylabel('h')
ax2.set_title('Duration')

runs_q_sum['count'].plot(ax=ax3, kind='bar', color='#7799cc')
ax3.set_ylabel('number')
ax3.set_title('Count')

fig.autofmt_xdate()

In [0]:
#@title Plot running activity, quarterly, mean

from matplotlib import ticker

fig2, (ax4, ax5) = (
    plt.subplots(
        nrows=2, ncols=1,
        sharex=True, sharey=False,
        figsize=(8.025, 10/3*2)))

(runs_q_sum['distance'] / runs_q_sum['count']).plot(ax=ax4, kind='bar', color='#7799cc');
ax4.set_ylabel('km')
ax4.set_title('Mean distance')
ax4.yaxis.set_major_locator(ticker.MultipleLocator(5))

(runs_q_sum['elapsed_time'] / runs_q_sum['count']).plot(ax=ax5, kind='bar', color='#7799cc');
ax5.set_ylabel('min')
ax5.set_title('Mean duration')
ax5.yaxis.set_major_locator(ticker.MultipleLocator(60))

fig2.autofmt_xdate()

In [0]:
#@title Plot running activity, quarterly, median
fig3, (ax6, ax7) = (
    plt.subplots(
        nrows=2, ncols=1,
        sharex=True, sharey=False,
        figsize=(8.025, 10/3*2)))

runs_q_median = (
    activities.loc[(slice(None), 'Run'), :]
        .reset_index('type', drop=True)
        .to_period('D')
        .groupby(pd.Grouper(freq='Q')).median())

runs_q_median['distance'].plot(ax=ax6, kind='bar', color='#7799cc')
ax6.set_ylabel('km')
ax6.set_title('Median distance')

runs_q_median['elapsed_time'].plot(ax=ax7, kind='bar', color='#7799cc')
ax7.set_ylabel('min')
ax7.set_title('Median duration')
ax7.yaxis.set_major_locator(ticker.MultipleLocator(30))

fig3.autofmt_xdate()

In [0]:
#@title Plot running activity, quarterly, pace
fig4, (ax8, ax9) = (
    plt.subplots(
        nrows=2, ncols=1,
        sharex=True, sharey=False,
        figsize=(8.025, 10/3*2)))

(runs_q_sum['elapsed_time'] / runs_q_sum['distance']).plot(ax=ax8, kind='bar', color='#7799cc');
ax8.set_ylabel('min / km')
ax8.set_title('Pace')

(runs_q_sum['distance'] / (runs_q_sum['elapsed_time'] / 60)).plot(ax=ax9, kind='bar', color='#7799cc');
ax9.set_ylabel('km / h')
ax9.set_title('Speed')

fig4.autofmt_xdate()

# Machine learning

Strava allows users to tag activities that were commutes. It is very easy to forget to tag an activity, which then reduces the quality of the collected data. Here, we will build a classifier which predicts whether an activity was a commute, so that we can go back to Strava and add missing tags if necessary. Thus we will consider any activity, even those which happened after the activity for which we predict the commute label; _leakage_ (not-a-time-machine) should not be an issue here.

In [0]:
#@title Split data into training and test

import sklearn
from sklearn.model_selection import train_test_split

X = activities.reset_index()[['date', 'type', 'distance', 'elapsed_time', 'name']]
y = activities.reset_index()['commute']

X_train, X_test, y_train, y_test = (
    train_test_split(
        X, y,
        train_size=0.8,
        test_size=0.2,
        random_state=314,
        shuffle=True))

In [0]:
#@title Extract features

import nltk
from nltk.stem import WordNetLemmatizer

nltk.download('wordnet')


def type_features(X):
  return pd.get_dummies(X[['type']])


def weekend_features(X):
  is_weekend = lambda d: d.dayofweek >= 5
  weekend = X['date'].apply(is_weekend)
  return pd.get_dummies(weekend, prefix='weekend')


def time_features(X):
  time = pd.cut(X['date'].apply(lambda d: d.hour),
                     right=False,
                     bins=[0, 6, 9, 12, 15, 18, 21, 24],
                     labels=['night',
                             'morning',
                             'late_morning',
                             'early_afternoon',
                             'late_afternoon',
                             'evening',
                             'late_evening'])
  return pd.get_dummies(time, prefix='time')


def distance_features(X):
  distance = pd.cut(X['distance'],
                    bins=np.logspace(1, 7, base=2, num=10),
                    labels=['xxxs', 'xxs',
                            'xs', 's', 'm',
                            'l', 'xl', 'xxl', 'xxxl'])
  return pd.get_dummies(distance, prefix='distance')


def duration_features(X):
  duration = pd.cut(X['elapsed_time'],
                    bins=np.logspace(4, 8, base=2, num=10),
                    labels=['xxxs', 'xxs',
                            'xs', 's', 'm',
                            'l', 'xl', 'xxl', 'xxxl'])
  return pd.get_dummies(duration, prefix='duration')


def word_features(X, train_indices):
  lemmatizer = WordNetLemmatizer()
  lemmatize_words = lambda s: [lemmatizer.lemmatize(w) for w in s]

  word_separators = r'[,:()!? ]'
  word_hyphenators = r'[\-_]'
  remove_short_words = lambda s: list(filter(lambda w: len(w) >= 5, s))
  make_unique = lambda s: list(set(s))
  prefix_with_word = lambda s: ['word_' + w for w in s]

  words = (
      X['name']
        .str.replace(word_separators, ' ')
        .str.replace(word_hyphenators, '')
        .str.lower()
        .str.split(' ')
        .apply(lambda s: [w.lower() for w in s])
        .apply(remove_short_words)
        .apply(make_unique)
        .apply(lemmatize_words)
        .apply(prefix_with_word)
        .apply(pd.Series)
        .stack()
        .reset_index(level=1, drop=True))

  words = words.reset_index().set_index(['index', 0])
  words['present'] = 1
  words = words.unstack(0, fill_value=0)
  words.columns.names = ['present', 'word']
  words.columns = words.columns.droplevel(level='present')

  # Correct for words only in test set; we could not possibly know
  # these words prior to prediction time.
  words_train = words.reindex(train_indices)
  words_only_in_test = (
      words_train.columns
          .to_series()
          .loc[words_train.sum() == 0]
          .index.values)
  words = words.drop(columns=words_only_in_test)
  return words


def features(X_features_list, train_index, test_index):
  X_features = pd.concat(X_features_list, axis=1).fillna(value=0)
  return (
      X_features.iloc[train_index],
      X_features.iloc[test_index]
  )


X_distance_duration_train, X_distance_duration_test = (
    features([
        distance_features(X),
        duration_features(X),
    ],
    X_train.index,
    X_test.index))

X_no_word_train, X_no_word_test = (
    features([
        type_features(X),
        weekend_features(X),
        time_features(X),
        distance_features(X),
        duration_features(X),
    ],
    X_train.index,
    X_test.index))

X_all_train, X_all_test = (
    features([
        type_features(X),
        weekend_features(X),
        time_features(X),
        distance_features(X),
        duration_features(X),
        word_features(X, X_train.index)
    ],
    X_train.index,
    X_test.index))

In [0]:
#@title Examine type features
print(
    pd.crosstab(
        type_features(X_train).idxmax(axis=1),
        y_train,
        rownames=[''],
        colnames=['commute']))

In [0]:
#@title Examine weekend features

print(
    pd.crosstab(
        weekend_features(X_train).idxmax(axis=1),
        y_train,
        rownames=[''],
        colnames=['commute']))

In [0]:
#@title Examine time features

print(
    pd.crosstab(
        time_features(X_train).idxmax(axis=1),
        y_train,
        rownames=[''],
        colnames=['commute']))

In [0]:
#@title Examine distance features

print(
    pd.crosstab(
        distance_features(X_train).idxmax(axis=1),
        y_train,
        rownames=[''],
        colnames=['commute']))

In [0]:
#@title Examine duration features

print(
    pd.crosstab(
        duration_features(X_train).idxmax(axis=1),
        y_train,
        rownames=[''],
        colnames=['commute']))

In [0]:
#@title Establish baseline

from sklearn.dummy import DummyClassifier

dummy = DummyClassifier('most_frequent')
dummy.fit(X_all_train, y_train)
dummy.score(X_all_train, y_train)

In [0]:
#@title Logistic Regression model

from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import GridSearchCV


def train_logistic_regression_model(X_features_train, y_train):
  lr_gs = GridSearchCV(LogisticRegression(random_state=99),
                           {'C': [0.01, 0.1, 1.0, 10, 100]},
                           scoring='roc_auc')
  lr_gs.fit(X_features_train, y_train)
  return lr_gs.best_estimator_, lr_gs.best_score_

In [0]:
#@title Naive Bayes classifier

from sklearn.naive_bayes import BernoulliNB


def train_naive_bayes_model(X_features_train, y_train):
  nb_gs = GridSearchCV(BernoulliNB(),
                       {'alpha': [0.001, 0.01, 0.1, 1, 10]},
                       scoring='roc_auc')
  nb_gs.fit(X_features_train, y_train)
  return nb_gs.best_estimator_, nb_gs.best_score_

In [0]:
#@title Support Vector Machine

from sklearn.svm import SVC


def train_support_vector_machine(X_features_train, y_train):
  svm_gs = GridSearchCV(SVC(probability=True, random_state=63),
                        {'C': [0.01, 0.1, 1, 10, 100],
                         'gamma': [0.001, 0.01, 0.1, 1, 10]},
                        scoring='roc_auc')
  svm_gs.fit(X_features_train, y_train)
  return svm_gs.best_estimator_, svm_gs.best_score_

In [0]:
#@title K-Nearest Neighbors

from sklearn.neighbors import KNeighborsClassifier


def train_knn_classifier(X_features_train, y_train):
  knn_gs = GridSearchCV(KNeighborsClassifier(p=1, weights='uniform'),
                        {'n_neighbors': [1, 3, 5, 7, 9, 11, 13, 15]},
                        scoring='roc_auc')
  knn_gs.fit(X_features_train, y_train)
  return knn_gs.best_estimator_, knn_gs.best_score_

In [0]:
#@title Decision tree

from sklearn.tree import DecisionTreeClassifier


def train_decision_tree(X_features_train, y_train):
  tree_gs = GridSearchCV(DecisionTreeClassifier(splitter='best', random_state=112),
                          {'min_samples_leaf': [5, 7, 9, 11, 13],
                           'max_depth': [None, 3, 5, 7, 9, 11]},
                          scoring='roc_auc')
  tree_gs.fit(X_features_train, y_train)
  return tree_gs.best_estimator_, tree_gs.best_score_

In [0]:
#@title Train models

from sklearn.model_selection import cross_val_score

training_functions = {
  'Logistic Regression': train_logistic_regression_model,
  'Naive Bayes': train_naive_bayes_model,
  'Support Vector Machine': train_support_vector_machine,
  'K-Nearest Neighbors': train_knn_classifier,
  'Decision Tree': train_decision_tree,
}

features_train = {
   'distance_duration': X_distance_duration_train,
   'no_word': X_no_word_train,
   'all': X_all_train,
}

models = []

for c, f in training_functions.items():
  for d, x in features_train.items():
    m_n = '%s_%s' % (c, d)
    print('Training classifier "%s" with features "%s"...' % (c, d))
    m, _ = f(x, y_train)
    models.append({
        'classifier': c,
        'features': d,
        'model': m,
    })

In [0]:
#@title Test models

from sklearn.metrics import f1_score
from sklearn.metrics import precision_score
from sklearn.metrics import recall_score
from sklearn.metrics import roc_auc_score

features_test = {
   'distance_duration': X_distance_duration_test,
   'no_word': X_no_word_test,
   'all': X_all_test,
}

for m in models:
  X_features_train = features_train[m['features']]
  X_features_test = features_test[m['features']]
  y_score_train = m['model'].predict_proba(X_features_train)[:, 1]
  y_pred_train = m['model'].predict(X_features_train)
  y_pred_test = m['model'].predict(X_features_test)
  y_score_test = m['model'].predict_proba(X_features_test)[:, 1]
  m['AUC (training)'] = roc_auc_score(y_train, y_score_train, average='micro')
  m['AUC (test)'] = roc_auc_score(y_test, y_score_test, average='micro')
  m['F1 (training)'] = f1_score(y_train, y_pred_train, average='micro')
  m['F1 (test)'] = f1_score(y_test, y_pred_test, average='micro')
  m['Precision (training)'] = precision_score(y_train, y_pred_train, average='micro')
  m['Precision (test)'] = precision_score(y_test, y_pred_test, average='micro')
  m['Recall (training)'] = recall_score(y_train, y_pred_train, average='micro')
  m['Recall (test)'] = recall_score(y_test, y_pred_test, average='micro')
  
models_df = pd.DataFrame.from_records(models, index=['classifier', 'features'])

In [0]:
#@title Plot AUC, F1, Precision, Recall

from matplotlib import ticker

def plot_scores(ax, models_df, features, score, title):
  (models_df
         .loc[(slice(None), features), score]
         .reset_index('features')
         .sort_index()
         .plot(ax=ax, kind='barh', title=title, legend=True))
  ax.set_ylabel('')
  ax.set_xlim(0, 1)
  ax.xaxis.set_major_locator(ticker.FixedLocator(np.linspace(0, 1, 6)))
  
def plot_all_scores(models_df, features):
  fig, ((ax1, ax2),
        (ax3, ax4)) = plt.subplots(nrows=2,
                                 ncols=2,
                                 sharex=True, 
                                 sharey=True,
                                 figsize=(6, 6))
  fig.suptitle('Feature set: %s' % features, fontsize=11, color='#444444')
  plot_scores(ax1, models_df, features, ['AUC (test)', 'AUC (training)'], 'AUC')
  plot_scores(ax2, models_df, features, ['F1 (test)', 'F1 (training)'], 'F1')
  plot_scores(ax3, models_df, features, ['Precision (test)', 'Precision (training)'], 'Precision')
  plot_scores(ax4, models_df, features, ['Recall (test)', 'Recall (training)'], 'Recall')

  
for f in features_test.keys():
  plot_all_scores(models_df, f)

fig.tight_layout()

In [0]:
#@title Inspect coefficients from Logistic Regression model

coef = pd.Series(models_df.loc[('Logistic Regression', 'no_word'), 'model'].coef_[0], index=X_no_word_train.columns)
print('\nPositive:')
print(coef.loc[coef > 0].sort_values(ascending=False))
print('\nNegative:')
print(coef.loc[coef < 0].sort_values(ascending=True))

In [0]:
#@title Plot ROC curves
from sklearn.metrics import roc_auc_score
from sklearn.metrics import roc_curve

def plot_roc_curve(ax, classifier, features):
  decision_function = (
      models_df.loc[(classifier, features), 'model']
               .decision_function(features_test[features]))
  fpr, tpr, _ = roc_curve(y_test, decision_function)
  ax.plot(fpr, tpr, color='darkorange', label='ROC curve')
  ax.fill_between(fpr, 0, tpr, color='#FFDFBA')
  ax.plot([0, 1], [0, 1], color='navy', lw=2, linestyle='--')
  ax.set_xlabel('False Positive Rate')
  ax.set_ylabel('True Positive Rate')
  ax.set_title('%s' % features)
  ax.legend(loc="lower right")
  
def plot_roc_curves_for_logistic_regression_and_svm():
  fig, ((ax1, ax2),
        (ax3, ax4),
        (ax5, ax6)) = plt.subplots(nrows=3,
                                 ncols=2,
                                 sharex=True, 
                                 sharey=True,
                                 figsize=(6, 9))

  plot_roc_curve(ax1, 'Logistic Regression', 'distance_duration')
  plot_roc_curve(ax2, 'Support Vector Machine', 'distance_duration')
  plot_roc_curve(ax3, 'Logistic Regression', 'no_word')
  plot_roc_curve(ax4, 'Support Vector Machine', 'no_word')
  plot_roc_curve(ax5, 'Logistic Regression', 'all')
  plot_roc_curve(ax6, 'Support Vector Machine', 'all')

  fig.tight_layout()

plot_roc_curves_for_logistic_regression_and_svm()